# Собираем датасет

In [ ]:
%%bash
#install libraries
pip install torchaudio
pip install wandb
pip install gdown

#download LjSpeech
wget https://data.keithito.com/data/speech/LJSpeech-1.1.tar.bz2 -o /dev/null
mkdir data
tar -xvf LJSpeech-1.1.tar.bz2 >> /dev/null
mv LJSpeech-1.1 data/LJSpeech-1.1

gdown https://drive.google.com/u/0/uc?id=1-EdH0t0loc6vPiuVtXdhsDtzygWNSNZx
mv train.txt data/

#download Waveglow
gdown https://drive.google.com/u/0/uc?id=1WsibBTsuRg_SF2Z6L6NFRTT-NjEy1oTx
mkdir -p waveglow/pretrained_model/
mv waveglow_256channels_ljs_v2.pt waveglow/pretrained_model/waveglow_256channels.pt

gdown https://drive.google.com/u/0/uc?id=1cJKJTmYd905a-9GFoo5gKjzhKjUVj83j
tar -xvf mel.tar.gz
echo $(ls mels | wc -l)

#download alignments
wget https://github.com/xcmyz/FastSpeech/raw/master/alignments.zip
unzip alignments.zip >> /dev/null

# we will use waveglow code, data and audio preprocessing from this repo
git clone https://github.com/xcmyz/FastSpeech.git
mv FastSpeech/text .
mv FastSpeech/audio .
mv FastSpeech/waveglow/* waveglow/
mv FastSpeech/utils.py .
mv FastSpeech/glow.py .
mv FastSpeech/hparams.py .

In [ ]:
# собираем датасет: текст, pitch, energy, duration, mel_spectrogram

!mkdir ./fastspeech2_dataset/
!cp ./data/train.txt ./fastspeech2_dataset/
!cp -r ./alignments ./fastspeech2_dataset/ # ./alignments/0.npy 0 ... 13099
!cp -r ./mels ./fastspeech2_dataset/ # ./mels/ljspeech-mel-00001.npy 1 ... 13100

In [ ]:
!mkdir ./fastspeech2_dataset/pitch
!mkdir ./fastspeech2_dataset/energy

In [ ]:
!pip install pyworld

In [ ]:
# pitch

import os
import soundfile as sf
import pyworld as pw
import numpy as np
import pandas as pd
from scipy.interpolate import interp1d

from tqdm import tqdm

frame_size = 1024
hop_size = 256
sample_rate = 22050

data = pd.read_csv('/content/data/LJSpeech-1.1/metadata.csv', sep='|', header=None)

for i in tqdm(range(len(data[0]))):
    filename = "./data/LJSpeech-1.1/wavs/" + data[0][i] + ".wav"
    audio, sr = sf.read(filename)

    f0, temp_pos = pw.dio(np.array(audio, dtype=np.float64), sr, frame_period=hop_size/sample_rate*1000)
    pitch = pw.stonemask(np.array(audio, dtype=np.float64), f0, temp_pos, sr)

    duration_name = "./fastspeech2_dataset/alignments/" + str(i) + ".npy"
    duration = np.load(duration_name)
    length = np.sum(duration)
    pitch = pitch[:length]

    #interpolate
    non_zero_ids = np.arange(len(pitch))[pitch != 0]
    interpolation = interp1d(non_zero_ids, pitch[non_zero_ids],
                             bounds_error=False,
                             fill_value=(pitch[non_zero_ids[0]], pitch[non_zero_ids[-1]]))
    pitch = interpolation(np.arange(len(pitch)))

    #log
    pitch = np.log(pitch)

    #normalize
    mean = pitch.mean()
    std = pitch.std()
    pitch = (pitch - mean) / (std + 1e-8)

    new_filename = "./fastspeech2_dataset/pitch/" + str(i) + ".npy"
    np.save(new_filename, np.array([mean, std] + pitch.tolist()))

100%|██████████| 13100/13100 [35:25<00:00,  6.16it/s]


In [ ]:
for i in tqdm(range(0, 13100)):
    align = np.load("./fastspeech2_dataset/alignments/" + str(i) + ".npy")
    mel = np.load("./fastspeech2_dataset/mels/ljspeech-mel-" + ("%05d" % (i+1)) + ".npy")
    assert align.sum() == mel.shape[0]

100%|██████████| 13100/13100 [00:38<00:00, 337.19it/s]


In [ ]:
for i in tqdm(range(0, 13100)):
    pitch = np.load("./fastspeech2_dataset/pitch/" + str(i) + ".npy")[2:]
    mel = np.load("./fastspeech2_dataset/mels/ljspeech-mel-" + ("%05d" % (i+1)) + ".npy")
    assert pitch.shape[0] == mel.shape[0]

100%|██████████| 13100/13100 [00:45<00:00, 290.86it/s]


In [ ]:
# energy

for i in tqdm(range(len(data[0]))):
    filename = "./fastspeech2_dataset/mels/ljspeech-mel-" + ("%05d" % (i + 1)) + ".npy"
    mel_spec = np.load(filename)
    energy = ((mel_spec ** 2).sum(-1))**0.5

    new_filename = "./fastspeech2_dataset/energy/" + str(i) + ".npy"
    np.save(new_filename, energy)

100%|██████████| 13100/13100 [00:41<00:00, 319.19it/s]


In [ ]:
for i in tqdm(range(0, 13100)):
    energy = np.load("./fastspeech2_dataset/energy/" + str(i) + ".npy")
    mel = np.load("./fastspeech2_dataset/mels/ljspeech-mel-" + ("%05d" % (i+1)) + ".npy")
    assert energy.shape[0] == mel.shape[0]

100%|██████████| 13100/13100 [00:41<00:00, 317.85it/s]


In [ ]:
# stats

max_pitch = -1e10
min_pitch = 1e10
max_energy = -1
min_energy = 1e20

for i in tqdm(range(0, 13100)):
    pitch = np.load("./fastspeech2_dataset/pitch/" + str(i) + ".npy")[2:]
    energy = np.load("./fastspeech2_dataset/energy/" + str(i) + ".npy")
    max_pitch = max(max_pitch, pitch.max())
    min_pitch = min(min_pitch, pitch.min())
    max_energy = max(max_energy, energy.max())
    min_energy = min(min_energy, energy.min())

max_pitch, min_pitch, max_energy, min_energy

100%|██████████| 13100/13100 [00:16<00:00, 815.76it/s] 


(7.497155011278676, -6.635588278343256, 91.4197, 15.023643)

In [ ]:
# !zip -r fastspeech2_dataset.zip ./fastspeech2_dataset
# !mkdir -p ./drive/MyDrive/dla_hw3/dataset/
# !cp fastspeech2_dataset.zip ./drive/MyDrive/dla_hw3/dataset/


# !gdown https://drive.google.com/u/0/uc?id=1-4cIK7IXOlpQYNqFoyF3RLMiy14JufGn
# !unzip fastspeech2_dataset.zip
# !rm -rf fastspeech2_dataset.zip

# Моделька (черновик)

In [ ]:
import pathlib
import random
import itertools
from tqdm import tqdm_notebook

from IPython import display
from dataclasses import dataclass

import torch
import torch.nn.functional as F
from torch import distributions
from torch import nn
from torch import optim
from torch.utils.data import Dataset, DataLoader

import torchaudio
from torchaudio.transforms import MelSpectrogram
import math
import time
import os
import librosa
import pandas as pd
from tqdm import tqdm
import numpy as np
from sklearn.model_selection import train_test_split
from matplotlib import pyplot as plt
from dataclasses import dataclass
from collections import OrderedDict

import seaborn as sns
sns.set()

import sys
sys.path.append('.')

In [ ]:
@dataclass
class MelSpectrogramConfig:
    num_mels = 80

@dataclass
class FastSpeech2Config:
    vocab_size = 300
    max_seq_len = 3000

    encoder_dim = 256
    encoder_n_layer = 4
    encoder_head = 2
    encoder_conv1d_filter_size = 1024

    decoder_dim = 256
    decoder_n_layer = 4
    decoder_head = 2
    decoder_conv1d_filter_size = 1024

    fft_conv1d_kernel = (9, 1)
    fft_conv1d_padding = (4, 0)

    duration_predictor_filter_size = 256
    duration_predictor_kernel_size = 3
    pitch_predictor_filter_size = 256
    pitch_predictor_kernel_size = 3
    energy_predictor_filter_size = 256
    energy_predictor_kernel_size = 3
    dropout = 0.1

    max_pitch = 7.5
    min_pitch = -6.7
    pitch_n_emb = 256
    max_energy = 91.5
    min_energy = 15.0
    energy_n_emb = 256

    PAD = 0
    UNK = 1
    BOS = 2
    EOS = 3

    PAD_WORD = '<blank>'
    UNK_WORD = '<unk>'
    BOS_WORD = '<s>'
    EOS_WORD = '</s>'


@dataclass
class TrainConfig:
    checkpoint_path = "./model_new"
    logger_path = "./logger"
    text_path = "./fastspeech2_dataset/train.txt"
    mel_path = "./fastspeech2_dataset/mels"
    alignment_path = "./fastspeech2_dataset/alignments"
    pitch_path = "./fastspeech2_dataset/pitch"
    energy_path = "./fastspeech2_dataset/energy"

    wandb_project = 'fastspeech2_example'

    text_cleaners = ['english_cleaners']

    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    device = 'cuda:0'

    batch_size = 16
    epochs = 2000
    n_warm_up_step = 4000

    learning_rate = 1e-3
    weight_decay = 1e-6
    grad_clip_thresh = 1.0
    decay_step = [500000, 1000000, 2000000]

    save_step = 3000
    log_step = 5
    clear_Time = 20

    batch_expand_size = 32


mel_config = MelSpectrogramConfig()
model_config = FastSpeech2Config()
train_config = TrainConfig()

In [ ]:
!pip install unidecode

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5/235.5 kB 3.5 MB/s eta 0:00:00


In [ ]:
from text import text_to_sequence


def pad_1D(inputs, PAD=0):

    def pad_data(x, length, PAD):
        x_padded = np.pad(x, (0, length - x.shape[0]),
                          mode='constant',
                          constant_values=PAD)
        return x_padded

    max_len = max((len(x) for x in inputs))
    padded = np.stack([pad_data(x, max_len, PAD) for x in inputs])

    return padded


def pad_1D_tensor(inputs, PAD=0):

    def pad_data(x, length, PAD):
        x_padded = F.pad(x, (0, length - x.shape[0]))
        return x_padded

    max_len = max((len(x) for x in inputs))
    padded = torch.stack([pad_data(x, max_len, PAD) for x in inputs])

    return padded


def pad_2D(inputs, maxlen=None):

    def pad(x, max_len):
        PAD = 0
        if np.shape(x)[0] > max_len:
            raise ValueError("not max_len")

        s = np.shape(x)[1]
        x_padded = np.pad(x, (0, max_len - np.shape(x)[0]),
                          mode='constant',
                          constant_values=PAD)
        return x_padded[:, :s]

    if maxlen:
        output = np.stack([pad(x, maxlen) for x in inputs])
    else:
        max_len = max(np.shape(x)[0] for x in inputs)
        output = np.stack([pad(x, max_len) for x in inputs])

    return output


def pad_2D_tensor(inputs, maxlen=None):

    def pad(x, max_len):
        if x.size(0) > max_len:
            raise ValueError("not max_len")

        s = x.size(1)
        x_padded = F.pad(x, (0, 0, 0, max_len-x.size(0)))
        return x_padded[:, :s]

    if maxlen:
        output = torch.stack([pad(x, maxlen) for x in inputs])
    else:
        max_len = max(x.size(0) for x in inputs)
        output = torch.stack([pad(x, max_len) for x in inputs])

    return output


def process_text(train_text_path):
    with open(train_text_path, "r", encoding="utf-8") as f:
        txt = []
        for line in f.readlines():
            txt.append(line)

        return txt


def get_data_to_buffer(train_config):
    buffer = list()
    text = process_text(train_config.text_path)

    start = time.perf_counter()
    for i in tqdm(range(len(text))):

        mel_gt_name = os.path.join(
            train_config.mel_path, "ljspeech-mel-%05d.npy" % (i+1))
        mel_gt_target = np.load(mel_gt_name)
        duration = np.load(os.path.join(
            train_config.alignment_path, str(i)+".npy"))
        pitch = np.load(os.path.join(
            train_config.pitch_path, str(i)+".npy"))
        pitch_mean = np.array([pitch[0]])
        pitch_std = np.array([pitch[1]])
        pitch = pitch[2:]
        energy = np.load(os.path.join(
            train_config.energy_path, str(i)+".npy"))

        character = text[i][0:len(text[i])-1]
        character = np.array(
            text_to_sequence(character, train_config.text_cleaners))

        character = torch.from_numpy(character)
        duration = torch.from_numpy(duration)
        pitch = torch.from_numpy(pitch)
        pitch_mean = torch.from_numpy(pitch_mean)
        pitch_std = torch.from_numpy(pitch_std)
        energy = torch.from_numpy(energy)
        mel_gt_target = torch.from_numpy(mel_gt_target)

        buffer.append({"text": character,
                       "duration": duration,
                       "pitch": pitch,
                       "pitch_mean": pitch_mean,
                       "pitch_std": pitch_std,
                       "energy": energy,
                       "mel_target": mel_gt_target})

    end = time.perf_counter()
    print("cost {:.2f}s to load all data into buffer.".format(end-start))

    return buffer


class BufferDataset(Dataset):
    def __init__(self, buffer):
        self.buffer = buffer
        self.length_dataset = len(self.buffer)

    def __len__(self):
        return self.length_dataset

    def __getitem__(self, idx):
        return self.buffer[idx]


def reprocess_tensor(batch, cut_list):
    texts = [batch[ind]["text"] for ind in cut_list]
    mel_targets = [batch[ind]["mel_target"] for ind in cut_list]
    durations = [batch[ind]["duration"] for ind in cut_list]
    pitches = [batch[ind]["pitch"] for ind in cut_list]
    pitch_means = [batch[ind]["pitch_mean"] for ind in cut_list]
    pitch_stds = [batch[ind]["pitch_std"] for ind in cut_list]
    energies = [batch[ind]["energy"] for ind in cut_list]

    length_text = np.array([])
    for text in texts:
        length_text = np.append(length_text, text.size(0))

    src_pos = list()
    max_len = int(max(length_text))
    for length_src_row in length_text:
        src_pos.append(np.pad([i+1 for i in range(int(length_src_row))],
                              (0, max_len-int(length_src_row)), 'constant'))
    src_pos = torch.from_numpy(np.array(src_pos))

    length_mel = np.array(list())
    for mel in mel_targets:
        length_mel = np.append(length_mel, mel.size(0))

    mel_pos = list()
    max_mel_len = int(max(length_mel))
    for length_mel_row in length_mel:
        mel_pos.append(np.pad([i+1 for i in range(int(length_mel_row))],
                              (0, max_mel_len-int(length_mel_row)), 'constant'))
    mel_pos = torch.from_numpy(np.array(mel_pos))

    texts = pad_1D_tensor(texts)
    mel_targets = pad_2D_tensor(mel_targets)
    durations = pad_1D_tensor(durations)
    pitches = pad_1D_tensor(pitches)
    pitch_means = torch.tensor(pitch_means)
    pitch_stds = torch.tensor(pitch_stds)
    energies = pad_1D_tensor(energies)

    out = {"text": texts,
           "mel_target": mel_targets,
           "duration": durations,
           "pitch": pitches,
           "pitch_mean": pitch_means,
           "pitch_std": pitch_stds,
           "energy": energies,
           "mel_pos": mel_pos,
           "src_pos": src_pos,
           "mel_max_len": max_mel_len}

    return out


def collate_fn_tensor(batch):
    len_arr = np.array([d["text"].size(0) for d in batch])
    index_arr = np.argsort(-len_arr)
    batchsize = len(batch)
    real_batchsize = batchsize // train_config.batch_expand_size

    cut_list = list()
    for i in range(train_config.batch_expand_size):
        cut_list.append(index_arr[i*real_batchsize:(i+1)*real_batchsize])

    output = list()
    for i in range(train_config.batch_expand_size):
        output.append(reprocess_tensor(batch, cut_list[i]))

    return output

/content/text/__init__.py:75: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  return s in _symbol_to_id and s is not '_' and s is not '~'
/content/text/__init__.py:75: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  return s in _symbol_to_id and s is not '_' and s is not '~'


In [ ]:
buffer = get_data_to_buffer(train_config)

dataset = BufferDataset(buffer)

training_loader = DataLoader(
    dataset,
    batch_size=train_config.batch_expand_size * train_config.batch_size,
    shuffle=True,
    collate_fn=collate_fn_tensor,
    drop_last=True,
    num_workers=0
)

100%|██████████| 13100/13100 [01:00<00:00, 217.43it/s]

cost 60.26s to load all data into buffer.


In [ ]:
batch = next(iter(training_loader))[0]
batch['text'].shape

torch.Size([16, 182])

In [ ]:
class ScaledDotProductAttention(nn.Module):
    ''' Scaled Dot-Product Attention '''

    def __init__(self, temperature, attn_dropout=0.1):
        super().__init__()
        self.temperature = temperature
        self.dropout = nn.Dropout(attn_dropout)
        self.softmax = nn.Softmax(dim=2)

    def forward(self, q, k, v, mask=None):
        # q, k, v: [ (batch_size * n_heads) x seq_len x hidden_size ]

        if mask is None:
            attn = self.softmax((q @ k.transpose(-1, -2)) / self.temperature)
        else:
            attn = self.softmax((q @ k.transpose(-1, -2)) / self.temperature) * ~mask

        # attn: [ (batch_size * n_heads) x seq_len x seq_len ]

        output = self.dropout(attn) @ v

        # output: [ (batch_size * n_heads) x seq_len x hidden_size ]
        return output, attn


class MultiHeadAttention(nn.Module):
    ''' Multi-Head Attention module '''

    def __init__(self, n_head, d_model, d_k, d_v, dropout=0.1):
        super().__init__()

        self.n_head = n_head
        self.d_k = d_k
        self.d_v = d_v
        self.d_model = d_model

        self.w_qs = nn.Linear(d_model, n_head * d_k)
        self.w_ks = nn.Linear(d_model, n_head * d_k)
        self.w_vs = nn.Linear(d_model, n_head * d_v)

        self.attention = ScaledDotProductAttention(
            temperature=d_k**0.5)
        self.layer_norm = nn.LayerNorm(d_model)

        self.fc = nn.Linear(n_head * d_v, d_model)
        nn.init.xavier_normal_(self.fc.weight)

        self.dropout = nn.Dropout(dropout)

        self.reset_parameters()

    def reset_parameters(self):
         # normal distribution initialization better than kaiming(default in pytorch)
        nn.init.normal_(self.w_qs.weight, mean=0,
                        std=np.sqrt(2.0 / (self.d_model + self.d_k)))
        nn.init.normal_(self.w_ks.weight, mean=0,
                        std=np.sqrt(2.0 / (self.d_model + self.d_k)))
        nn.init.normal_(self.w_vs.weight, mean=0,
                        std=np.sqrt(2.0 / (self.d_model + self.d_v)))

    def forward(self, q, k, v, mask=None):
        d_k, d_v, n_head = self.d_k, self.d_v, self.n_head

        sz_b, len_q, _ = q.size()
        sz_b, len_k, _ = k.size()
        sz_b, len_v, _ = v.size()

        residual = q

        q = self.w_qs(q).view(sz_b, len_q, n_head, d_k)
        k = self.w_ks(k).view(sz_b, len_k, n_head, d_k)
        v = self.w_vs(v).view(sz_b, len_v, n_head, d_v)

        q = q.permute(2, 0, 1, 3).contiguous().view(-1, len_q, d_k)  # (n*b) x lq x dk
        k = k.permute(2, 0, 1, 3).contiguous().view(-1, len_k, d_k)  # (n*b) x lk x dk
        v = v.permute(2, 0, 1, 3).contiguous().view(-1, len_v, d_v)  # (n*b) x lv x dv

        if mask is not None:
            mask = mask.repeat(n_head, 1, 1)  # (n*b) x .. x ..
        output, attn = self.attention(q, k, v, mask=mask)

        output = output.view(n_head, sz_b, len_q, d_v)
        output = output.permute(1, 2, 0, 3).contiguous().view(sz_b, len_q, -1)  # b x lq x (n*dv)

        output = self.dropout(self.fc(output))
        output = self.layer_norm(output + residual)

        return output, attn


class PositionwiseFeedForward(nn.Module):
    ''' A two-feed-forward-layer module '''

    def __init__(self, d_in, d_hid, dropout=0.1):
        super().__init__()

        # Use Conv1D
        # position-wise
        self.w_1 = nn.Conv1d(
            d_in, d_hid, kernel_size=model_config.fft_conv1d_kernel[0], padding=model_config.fft_conv1d_padding[0])
        # position-wise
        self.w_2 = nn.Conv1d(
            d_hid, d_in, kernel_size=model_config.fft_conv1d_kernel[1], padding=model_config.fft_conv1d_padding[1])

        self.layer_norm = nn.LayerNorm(d_in)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        residual = x
        output = x.transpose(1, 2)
        output = self.w_2(F.relu(self.w_1(output)))
        output = output.transpose(1, 2)
        output = self.dropout(output)
        output = self.layer_norm(output + residual)

        return output


class FFTBlock(torch.nn.Module):
    """FFT Block"""

    def __init__(self,
                 d_model,
                 d_inner,
                 n_head,
                 d_k,
                 d_v,
                 dropout=0.1):
        super(FFTBlock, self).__init__()
        self.slf_attn = MultiHeadAttention(
            n_head, d_model, d_k, d_v, dropout=dropout)
        self.pos_ffn = PositionwiseFeedForward(
            d_model, d_inner, dropout=dropout)

    def forward(self, enc_input, non_pad_mask=None, slf_attn_mask=None):
        enc_output, enc_slf_attn = self.slf_attn(
            enc_input, enc_input, enc_input, mask=slf_attn_mask)

        if non_pad_mask is not None:
            enc_output *= non_pad_mask

        enc_output = self.pos_ffn(enc_output)

        if non_pad_mask is not None:
            enc_output *= non_pad_mask

        return enc_output, enc_slf_attn

In [ ]:
def create_alignment(base_mat, duration_predictor_output):
    N, L = duration_predictor_output.shape
    for i in range(N):
        count = 0
        for j in range(L):
            for k in range(duration_predictor_output[i][j]):
                base_mat[i][count+k][j] = 1
            count = count + duration_predictor_output[i][j]
    return base_mat


class Transpose(nn.Module):
    def __init__(self, dim_1, dim_2):
        super().__init__()
        self.dim_1 = dim_1
        self.dim_2 = dim_2

    def forward(self, x):
        return x.transpose(self.dim_1, self.dim_2)


class DurationPredictor(nn.Module):
    """ Duration Predictor """

    def __init__(self, model_config: FastSpeech2Config):
        super(DurationPredictor, self).__init__()

        self.input_size = model_config.encoder_dim
        self.filter_size = model_config.duration_predictor_filter_size
        self.kernel = model_config.duration_predictor_kernel_size
        self.conv_output_size = model_config.duration_predictor_filter_size
        self.dropout = model_config.dropout

        self.conv_net = nn.Sequential(
            Transpose(-1, -2),
            nn.Conv1d(
                self.input_size, self.filter_size,
                kernel_size=self.kernel, padding=1
            ),
            Transpose(-1, -2),
            nn.ReLU(),
            nn.LayerNorm(self.filter_size),
            nn.Dropout(self.dropout),
            Transpose(-1, -2),
            nn.Conv1d(
                self.filter_size, self.filter_size,
                kernel_size=self.kernel, padding=1
            ),
            Transpose(-1, -2),
            nn.ReLU(),
            nn.LayerNorm(self.filter_size),
            nn.Dropout(self.dropout)
        )

        self.linear_layer = nn.Linear(self.conv_output_size, 1)

    def forward(self, encoder_output):
        encoder_output = self.conv_net(encoder_output)

        out = self.linear_layer(encoder_output)
        out = out.squeeze()
        if not self.training:
            out = out.unsqueeze(0)
        return out


class LengthRegulator(nn.Module):
    """ Length Regulator """

    def __init__(self, model_config):
        super(LengthRegulator, self).__init__()
        self.duration_predictor = DurationPredictor(model_config)

    def LR(self, x, duration_predictor_output, mel_max_length=None):
        expand_max_len = torch.max(
            torch.sum(duration_predictor_output, -1), -1)[0]
        alignment = torch.zeros(duration_predictor_output.size(0),
                                expand_max_len,
                                duration_predictor_output.size(1)).numpy()
        alignment = create_alignment(alignment,
                                     duration_predictor_output.cpu().numpy())
        alignment = torch.from_numpy(alignment).to(x.device)

        output = alignment @ x
        if mel_max_length:
            output = F.pad(
                output, (0, 0, 0, mel_max_length-output.size(1), 0, 0))
        return output

    def forward(self, x, alpha=1.0, target=None, mel_max_length=None):
        durations = torch.exp(self.duration_predictor(x)) * alpha
        if target is not None:
            if target.shape[1] != durations.shape[1]:
                new_target = F.pad(target, (0, durations.shape[-1] - target.shape[-1])) * alpha
            else:
                new_target = target * alpha
            duration_predictor_output = torch.round(new_target).int()
        else:
            duration_predictor_output = torch.round(durations).int()
        output = self.LR(x, duration_predictor_output, mel_max_length)
        return output, duration_predictor_output, durations

In [ ]:
def get_non_pad_mask(seq):
    assert seq.dim() == 2
    return seq.ne(model_config.PAD).type(torch.float).unsqueeze(-1)

def get_attn_key_pad_mask(seq_k, seq_q):
    ''' For masking out the padding part of key sequence. '''
    # Expand to fit the shape of key query attention matrix.
    len_q = seq_q.size(1)
    padding_mask = seq_k.eq(model_config.PAD)
    padding_mask = padding_mask.unsqueeze(
        1).expand(-1, len_q, -1)  # b x lq x lk

    return padding_mask


class Encoder(nn.Module):
    def __init__(self, model_config):
        super(Encoder, self).__init__()

        len_max_seq=model_config.max_seq_len
        n_position = len_max_seq + 1
        n_layers = model_config.encoder_n_layer

        self.src_word_emb = nn.Embedding(
            model_config.vocab_size,
            model_config.encoder_dim,
            padding_idx=model_config.PAD
        )

        self.position_enc = nn.Embedding(
            n_position,
            model_config.encoder_dim,
            padding_idx=model_config.PAD
        )

        self.layer_stack = nn.ModuleList([FFTBlock(
            model_config.encoder_dim,
            model_config.encoder_conv1d_filter_size,
            model_config.encoder_head,
            model_config.encoder_dim // model_config.encoder_head,
            model_config.encoder_dim // model_config.encoder_head,
            dropout=model_config.dropout
        ) for _ in range(n_layers)])

    def forward(self, src_seq, src_pos, return_attns=False):

        enc_slf_attn_list = []

        # -- Prepare masks
        slf_attn_mask = get_attn_key_pad_mask(seq_k=src_seq, seq_q=src_seq)
        non_pad_mask = get_non_pad_mask(src_seq)

        # -- Forward
        enc_output = self.src_word_emb(src_seq) + self.position_enc(src_pos)

        for enc_layer in self.layer_stack:
            enc_output, enc_slf_attn = enc_layer(
                enc_output,
                non_pad_mask=non_pad_mask,
                slf_attn_mask=slf_attn_mask)
            if return_attns:
                enc_slf_attn_list += [enc_slf_attn]

        return enc_output, non_pad_mask


class Decoder(nn.Module):
    """ Decoder """

    def __init__(self, model_config):

        super(Decoder, self).__init__()

        len_max_seq=model_config.max_seq_len
        n_position = len_max_seq + 1
        n_layers = model_config.decoder_n_layer

        self.position_enc = nn.Embedding(
            n_position,
            model_config.encoder_dim,
            padding_idx=model_config.PAD,
        )

        self.layer_stack = nn.ModuleList([FFTBlock(
            model_config.encoder_dim,
            model_config.encoder_conv1d_filter_size,
            model_config.encoder_head,
            model_config.encoder_dim // model_config.encoder_head,
            model_config.encoder_dim // model_config.encoder_head,
            dropout=model_config.dropout
        ) for _ in range(n_layers)])

    def forward(self, enc_seq, enc_pos, return_attns=False):

        dec_slf_attn_list = []

        # -- Prepare masks
        slf_attn_mask = get_attn_key_pad_mask(seq_k=enc_pos, seq_q=enc_pos)
        non_pad_mask = get_non_pad_mask(enc_pos)

        # -- Forward
        dec_output = enc_seq + self.position_enc(enc_pos)

        for dec_layer in self.layer_stack:
            dec_output, dec_slf_attn = dec_layer(
                dec_output,
                non_pad_mask=non_pad_mask,
                slf_attn_mask=slf_attn_mask)
            if return_attns:
                dec_slf_attn_list += [dec_slf_attn]

        return dec_output

In [ ]:
class PitchPredictor(nn.Module):

    def __init__(self, model_config: FastSpeech2Config):
        super(PitchPredictor, self).__init__()

        self.input_size = model_config.encoder_dim
        self.filter_size = model_config.pitch_predictor_filter_size
        self.kernel = model_config.pitch_predictor_kernel_size
        self.conv_output_size = model_config.pitch_predictor_filter_size
        self.dropout = model_config.dropout

        self.conv_net = nn.Sequential(
            Transpose(-1, -2),
            nn.Conv1d(
                self.input_size, self.filter_size,
                kernel_size=self.kernel, padding=1
            ),
            Transpose(-1, -2),
            nn.ReLU(),
            nn.LayerNorm(self.filter_size),
            nn.Dropout(self.dropout),
            Transpose(-1, -2),
            nn.Conv1d(
                self.filter_size, self.filter_size,
                kernel_size=self.kernel, padding=1
            ),
            Transpose(-1, -2),
            nn.ReLU(),
            nn.LayerNorm(self.filter_size),
            nn.Dropout(self.dropout)
        )

        self.linear_layer = nn.Linear(self.conv_output_size, 1)
        self.mean_pred = nn.Linear(self.conv_output_size, 1)
        self.std_pred = nn.Linear(self.conv_output_size, 1)

    def forward(self, encoder_output):
        encoder_output = self.conv_net(encoder_output)

        out = self.linear_layer(encoder_output)
        mean = self.mean_pred(encoder_output.mean(1))
        std = self.std_pred(encoder_output.mean(1))
        out = out.squeeze()
        if not self.training:
            out = out.unsqueeze(0)
        return out, mean, std


class EnergyPredictor(nn.Module):

    def __init__(self, model_config: FastSpeech2Config):
        super(EnergyPredictor, self).__init__()

        self.input_size = model_config.encoder_dim
        self.filter_size = model_config.pitch_predictor_filter_size
        self.kernel = model_config.pitch_predictor_kernel_size
        self.conv_output_size = model_config.pitch_predictor_filter_size
        self.dropout = model_config.dropout

        self.conv_net = nn.Sequential(
            Transpose(-1, -2),
            nn.Conv1d(
                self.input_size, self.filter_size,
                kernel_size=self.kernel, padding=1
            ),
            Transpose(-1, -2),
            nn.ReLU(),
            nn.LayerNorm(self.filter_size),
            nn.Dropout(self.dropout),
            Transpose(-1, -2),
            nn.Conv1d(
                self.filter_size, self.filter_size,
                kernel_size=self.kernel, padding=1
            ),
            Transpose(-1, -2),
            nn.ReLU(),
            nn.LayerNorm(self.filter_size),
            nn.Dropout(self.dropout)
        )

        self.linear_layer = nn.Linear(self.conv_output_size, 1)

    def forward(self, encoder_output):
        encoder_output = self.conv_net(encoder_output)

        out = self.linear_layer(encoder_output)
        out = out.squeeze()
        if not self.training:
            out = out.unsqueeze(0)
        return out

In [ ]:
def get_mask_from_lengths(lengths, max_len=None):
    if max_len == None:
        max_len = torch.max(lengths).item()

    ids = torch.arange(0, max_len, 1, device=lengths.device)
    mask = (ids < lengths.unsqueeze(1)).bool()

    return mask


class FastSpeech2(nn.Module):

    def __init__(self, model_config):
        super(FastSpeech2, self).__init__()

        self.encoder = Encoder(model_config)

        self.length_regulator = LengthRegulator(model_config)

        self.pitch_predictor = PitchPredictor(model_config)
        self.pitch_embed = nn.Embedding(model_config.pitch_n_emb,
                                        model_config.encoder_dim)
        self.pitch_boundaries = torch.linspace(model_config.min_pitch,
                                          model_config.max_pitch,
                                          model_config.pitch_n_emb + 1).unsqueeze(0).unsqueeze(0)

        self.energy_predictor = EnergyPredictor(model_config)
        self.energy_embed = nn.Embedding(model_config.energy_n_emb,
                                        model_config.encoder_dim)
        self.energy_boundaries = torch.linspace(model_config.min_energy,
                                           model_config.max_energy,
                                           model_config.energy_n_emb + 1).unsqueeze(0).unsqueeze(0)
        self.decoder = Decoder(model_config)

        self.mel_linear = nn.Linear(model_config.decoder_dim, mel_config.num_mels)

    def mask_tensor(self, mel_output, position, mel_max_length):
        lengths = torch.max(position, -1)[0]
        mask = ~get_mask_from_lengths(lengths, max_len=mel_max_length)
        mask = mask.unsqueeze(-1).expand(-1, -1, mel_output.size(-1))
        return mel_output.masked_fill(mask, 0.)

    def forward(self, src_seq, src_pos,
                mel_pos=None, mel_max_length=None,
                target_duration=None,
                target_pitch=None,
                target_pitch_mean=None,
                target_pitch_std=None,
                target_energy=None,
                alpha=1.0):
        self.pitch_boundaries = self.pitch_boundaries.to(src_seq.device)
        self.energy_boundaries = self.energy_boundaries.to(src_seq.device)

        enc_output, non_pad_mask = self.encoder(src_seq, src_pos)

        lr_output, duration_predictor_output, durations = self.length_regulator(enc_output, alpha, target_duration, mel_max_length)
        got_expansion = duration_predictor_output.sum(-1).cpu()
        new_enc_pos = list()
        max_new_enc_pos = lr_output.shape[1]
        for i in range(got_expansion.shape[0]):
            new_enc_pos.append(np.pad([i+1 for i in range(int(got_expansion[i].item()))],
                                      (0, max_new_enc_pos-int(got_expansion[i].item())), 'constant'))
        new_enc_pos = torch.from_numpy(np.array(new_enc_pos)).to(lr_output.device)

        pitch, mean, std = self.pitch_predictor(lr_output)
        if target_pitch is not None:
            new_pitch = (target_pitch * target_pitch_std.unsqueeze(-1) + \
                         target_pitch_mean.unsqueeze(-1)).unsqueeze(-1).repeat(1, 1, self.pitch_boundaries.shape[-1])
        else:
            new_pitch = (pitch * std.unsqueeze(-1) + \
                         mean.unsqueeze(-1)).unsqueeze(-1).repeat(1, 1, self.pitch_boundaries.shape[-1])
        pitch_ids = (~(new_pitch < self.pitch_boundaries)).sum(-1) - 1
        pitch_ids = torch.maximum(pitch_ids, torch.zeros_like(pitch_ids).to(pitch_ids.device)).long()
        pitch_output = self.pitch_embed(pitch_ids)
        pitch_output = self.mask_tensor(pitch_output, new_enc_pos, mel_max_length)

        energy = self.energy_predictor(lr_output)
        if target_energy is not None:
            new_energy = target_energy.unsqueeze(-1).repeat(1, 1, self._boundaries.shape[-1])
        else:
            new_energy = energy.unsqueeze(-1).repeat(1, 1, self.energy_boundaries.shape[-1])
        energy_ids = (~(new_energy < self.energy_boundaries)).sum(-1) - 1
        energy_ids = torch.maximum(energy_ids, torch.zeros_like(energy_ids).to(energy_ids.device)).long()
        energy_output = self.energy_embed(energy_ids)
        energy_output = self.mask_tensor(energy_output, new_enc_pos, mel_max_length)

        output = lr_output + pitch_output + energy_output

        dec_output = self.mel_linear(self.decoder(output, new_enc_pos))
        if target_duration is not None: # training
            dec_output = self.mask_tensor(dec_output, mel_pos, mel_max_length)
        else:
            dec_output = self.mask_tensor(dec_output, new_enc_pos, mel_max_length)
        return dec_output, durations, pitch, mean, std, energy

In [ ]:
import torch
import torch.nn as nn


class FastSpeech2Loss(nn.Module):
    def __init__(self):
        super().__init__()
        self.mse_loss = nn.MSELoss()
        self.l1_loss = nn.L1Loss()

    def forward(self, mel, duration_predicted,
                pitch_predicted, pitch_mean_predicted, pitch_std_predicted,
                energy_predicted,
                mel_target, duration_target,
                pitch_target, pitch_mean_target, pitch_std_target,
                energy_target):
        mel_loss = self.l1_loss(mel, mel_target)
        pitch_loss = self.mse_loss(pitch_predicted, pitch_target)
        pitch_mean_loss = self.mse_loss(pitch_mean_predicted, pitch_mean_target)
        pitch_std_loss = self.mse_loss(pitch_std_predicted, pitch_std_target)
        energy_loss = self.mse_loss(energy_predicted, energy_target)
        duration_loss = self.mse_loss(duration_predicted, duration_target.float())

        return mel_loss, duration_loss, pitch_loss, pitch_mean_loss, pitch_std_loss, energy_loss

In [ ]:
!pip install wandb

In [ ]:
from torch.optim.lr_scheduler  import OneCycleLR
from wandb_writer import WanDBWriter

In [ ]:
logger = WanDBWriter(train_config)

<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: akhmatovaanna2002 (team-from-wonderland). Use `wandb login --relogin` to force relogin


In [ ]:
model = FastSpeech2(model_config)
model = model.to(train_config.device)

fastspeech_loss = FastSpeech2Loss()
current_step = 0

optimizer = torch.optim.AdamW(
    model.parameters(),
    lr=train_config.learning_rate,
    betas=(0.9, 0.98),
    eps=1e-9)

scheduler = OneCycleLR(optimizer, **{
    "steps_per_epoch": len(training_loader) * train_config.batch_expand_size,
    "epochs": train_config.epochs,
    "anneal_strategy": "cos",
    "max_lr": train_config.learning_rate,
    "pct_start": 0.1
})

In [ ]:
!mkdir ./model_new

In [ ]:
tqdm_bar = tqdm(total=train_config.epochs * len(training_loader) * train_config.batch_expand_size - current_step)


for epoch in range(train_config.epochs):
    for i, batchs in enumerate(training_loader):
        # real batch start here
        for j, db in enumerate(batchs):
            current_step += 1
            tqdm_bar.update(1)

            logger.set_step(current_step)

            # Get Data
            character = db["text"].long().to(train_config.device)
            mel_target = db["mel_target"].float().to(train_config.device)
            duration = db["duration"].long().to(train_config.device)
            pitch = db["pitch"].float().to(train_config.device)
            pitch_mean = db["pitch_mean"].float().to(train_config.device)
            pitch_std = db["pitch_std"].float().to(train_config.device)
            energy = db["energy"].float().to(train_config.device)
            mel_pos = db["mel_pos"].long().to(train_config.device)
            src_pos = db["src_pos"].long().to(train_config.device)
            max_mel_len = db["mel_max_len"]

            # Forward
            preds = model(character,
                          src_pos,
                          mel_pos=mel_pos,
                          mel_max_length=max_mel_len,
                          target_duration=duration,
                          target_pitch=pitch,
                          target_pitch_mean=pitch_mean,
                          target_pitch_std=pitch_std,
                          target_energy=energy,
                          alpha=1.0)

            mel_pred, durations_pred, pitch_pred, pitch_mean_pred, pitch_std_pred, energy_pred = preds

            # Calc Loss
            losses = fastspeech_loss(mel_pred,
                                     durations_pred,
                                     pitch_pred,
                                     pitch_mean_pred,
                                     pitch_std_pred,
                                     energy_pred,
                                     mel_target,
                                     duration,
                                     pitch,
                                     pitch_mean,
                                     pitch_std,
                                     energy)

            mel_loss, duration_loss, pitch_loss, pitch_mean_loss, pitch_std_loss, energy_loss = losses

            total_loss = mel_loss + duration_loss + pitch_loss + pitch_mean_loss + pitch_std_loss + energy_loss

            # Logger
            t_l = total_loss.detach().cpu().numpy()
            m_l = mel_loss.detach().cpu().numpy()
            d_l = duration_loss.detach().cpu().numpy()
            p_l = pitch_loss.detach().cpu().numpy()
            pm_l = pitch_mean_loss.detach().cpu().numpy()
            ps_l = pitch_std_loss.detach().cpu().numpy()
            e_l = energy_loss.detach().cpu().numpy()

            logger.add_scalar("duration_loss", d_l)
            logger.add_scalar("mel_loss", m_l)
            logger.add_scalar("total_loss", t_l)
            logger.add_scalar("pitch_loss", p_l)
            logger.add_scalar("pitch_mean_loss", pm_l)
            logger.add_scalar("pitch_std_loss", ps_l)
            logger.add_scalar("energy_loss", e_l)

            # Backward
            total_loss.backward()

            # Clipping gradients to avoid gradient explosion
            nn.utils.clip_grad_norm_(
                model.parameters(), train_config.grad_clip_thresh)

            optimizer.step()
            optimizer.zero_grad(set_to_none=True)
            scheduler.step()

            if current_step % train_config.save_step == 0:
                torch.save({'model': model.state_dict(), 'optimizer': optimizer.state_dict(
                )}, os.path.join(train_config.checkpoint_path, 'checkpoint_%d.pth.tar' % current_step))
                print("save model at step %d ..." % current_step)



  0%|          | 1/1600000 [04:44<126376:14:01, 284.35s/it]

  0%|          | 1/1600000 [00:00<144:53:14,  3.07it/s]/usr/local/lib/python3.10/dist-packages/torch/nn/modules/loss.py:535: UserWarning: Using a target size (torch.Size([16])) that is different to the input size (torch.Size([16, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)

  0%|          | 3001/1600000 [17:37<246:13:14,  1.80it/s]

save model at step 3000 ...



  0%|          | 6001/1600000 [35:39<316:11:48,  1.40it/s]

save model at step 6000 ...



  1%|          | 9001/1600000 [53:48<279:22:05,  1.58it/s]

...


  3%|▎         | 51001/1600000 [5:10:46<222:19:03,  1.94it/s]

save model at step 51000 ...



  3%|▎         | 54001/1600000 [5:29:17<318:50:30,  1.35it/s]

save model at step 54000 ...



  4%|▎         | 56517/1600000 [5:44:52<187:44:20,  2.28it/s]

# Установка

In [ ]:
%%bash

pip install -r requirements.txt
pip install .

gdown https://drive.google.com/u/0/uc?id=1-4cIK7IXOlpQYNqFoyF3RLMiy14JufGn
unzip fastspeech2_dataset.zip
rm -rf fastspeech2_dataset.zip

gdown https://drive.google.com/u/0/uc?id=1WsibBTsuRg_SF2Z6L6NFRTT-NjEy1oTx
mkdir -p waveglow/pretrained_model/
mv waveglow_256channels_ljs_v2.pt waveglow/pretrained_model/waveglow_256channels.pt

git clone https://github.com/xcmyz/FastSpeech.git
mv ./FastSpeech/text .
mv ./FastSpeech/audio .
mv ./FastSpeech/waveglow/* waveglow/
mv ./FastSpeech/utils.py .
mv ./FastSpeech/glow.py .
mv ./FastSpeech/hparams.py .
rm -rf ./FastSpeech/